In [1]:
import torch
import schnetpack as spk
import math
from schnetpack.datasets import QM9


import numpy as np
from numpy import savetxt

# Define Important Functions

In [2]:
def print_molecule(props):
    
    # load x,y,z coordinates tensors
    x = props['_positions'][ :,0]
    y = props['_positions'][ :,1]
    z = props['_positions'][ :,2]
    x = x.numpy()
    y = y.numpy()
    z = z.numpy()
    
    for i in range(len(z)):
        if props['_atomic_numbers'][i] == 1:
            print('H',x[i],y[i],z[i])
        if props['_atomic_numbers'][i] == 6:
            print('C',x[i],y[i],z[i])
        if props['_atomic_numbers'][i] == 7:
            print('N',x[i],y[i],z[i])     
        if props['_atomic_numbers'][i] == 8:
            print('O',x[i],y[i],z[i])
        if props['_atomic_numbers'][i] == 9:
            print('F',x[i],y[i],z[i]) 
    print('')  
    return x,y,z

def hook_v0(self, inp_tensor, out_tensor):
    # Self is included and refers to the model class
    # Global allows us to utilize embedding_output outside the current function scope
    global v0
    #Update the embedding_output variable to be equal to our output tensor
    v0=out_tensor 

def hook_v1(self, inp_tensor, out_tensor):
    # Self is included and refers to the model class
    # Global allows us to utilize embedding_output outside the current function scope
    global v1
    #Update the embedding_output variable to be equal to our output tensor
    v1=out_tensor 

def hook_v2(self, inp_tensor, out_tensor):
    # Self is included and refers to the model class
    # Global allows us to utilize embedding_output outside the current function scope
    global v2
    #Update the embedding_output variable to be equal to our output tensor
    v2=out_tensor  
    
def hook_emb(self, inp_tensor, out_tensor):
    # Self is included and refers to the model class
    # Global allows us to utilize embedding_output outside the current function scope
    global emb
    #Update the embedding_output variable to be equal to our output tensor
    emb=out_tensor 
#def convert_2D(number_of_atoms,rep):
#    layer = np.zeros((number_of_atoms,30))
#    for i in range(number_of_atoms):
#        for j in range(30):
#            layer[i][j] = rep[0][i][j]
#    return layer



In [3]:
qm9data = QM9('./qm9.db', download=True, remove_uncharacterized=True)
checkpoint_path = '../../../../data/trained_models/qm9_i3_30f_10000_5000/trained.pth'
split_file='../../../../data/trained_models/qm9_i3_30f_10000_5000/split.npz'
number_of_inputs = 10000

# Load split file 
train, val, test = spk.data.train_test_split(qm9data,split_file=split_file)

# Load atom ref data 
atomrefs = qm9data.get_atomref(QM9.U0)
print('U0 of hyrogen:', '{:.2f}'.format(atomrefs[QM9.U0][1][0]), 'eV')
print('U0 of carbon:', '{:.2f}'.format(atomrefs[QM9.U0][6][0]), 'eV')
print('U0 of oxygen:', '{:.2f}'.format(atomrefs[QM9.U0][8][0]), 'eV')
print('U0 of oxygen:', '{:.2f}'.format(atomrefs[QM9.U0][7][0]), 'eV')   

# Define SchNet representation model

schnet = spk.representation.SchNet(
    n_atom_basis=30, n_filters=30, n_gaussians=20, n_interactions=3,
    cutoff=4. , cutoff_network=spk.nn.cutoff.CosineCutoff
)

# Define SchNet output model and property to be predicted

output_U0 = spk.atomistic.Atomwise(n_in=30, atomref=atomrefs[QM9.U0])

# Define atomistic model

model = spk.AtomisticModel(representation=schnet,output_modules=output_U0)

# Load saved checkpoint file
load_checkpoint = torch.load(checkpoint_path)

#qm9_i6_30f_20g-1000-500-4_300.pth
# load model's state dictionary from saved checkpoint
model.load_state_dict(load_checkpoint)

#set up device for forward pass
device='cpu'

# load atoms converter 
converter = spk.data.AtomsConverter(device=device)

datao = np.zeros((1,30))
datahae = np.zeros((1))
dataoae = np.zeros((1))
datah = np.zeros((1,30))
data = np.zeros((1))

datac = np.zeros((1,30))
datacae = np.zeros((1))

datan = np.zeros((1,30))
datanae = np.zeros((1))
for idx in range(number_of_inputs):

    # load data for molecule
    at, props = qm9data.get_properties(idx)

    
    # print molecule for identification
    print(idx)
    x, y, z = print_molecule(props)
    number_of_atoms=len(z)

    # convert qm9 data to machine-readable form
    inputs = converter(at)

    #Instatiate layer output
    v0=None
    v1=None
    v2=None
    x=None       

    # Forward hook the model's interaction layer 
    model.representation.interactions[0].register_forward_hook(hook_v0)

    # Forward hook the model's interaction layer 
    model.representation.interactions[1].register_forward_hook(hook_v1)

    # Forward hook the model's interaction layer 
    model.representation.interactions[2].register_forward_hook(hook_v2)

    # Forward hook the model's interaction layer 
    model.representation.embedding.register_forward_hook(hook_emb)

    # Forward pass molecules through the model
    model(inputs)


    rep = emb + v0 + v1 + v2
    rows = np.zeros((number_of_atoms,30))
    for i in range(number_of_atoms):
        for j in range(30):
            rows[i][j] = rep[0][i][j]

    from schnetpack.atomistic.output_modules import yi

    yi=yi.detach().numpy()

    #save the vector of every oxygen atom encountered
    for i in range(number_of_atoms):
        if props['_atomic_numbers'][i] == 8:
            datao = np.vstack((datao,rows[i]))
    for i in range(number_of_atoms):
        if props['_atomic_numbers'][i] == 1:
            datah = np.vstack((datah,rows[i]))    
    for i in range(number_of_atoms):
        if props['_atomic_numbers'][i] == 1:
            datahae = np.vstack((datahae,yi[0][i]))
    for i in range(number_of_atoms):
        if props['_atomic_numbers'][i] == 8:
            dataoae = np.vstack((dataoae,yi[0][i]))

    for i in range(number_of_atoms):
        if props['_atomic_numbers'][i] == 6:
            datac = np.vstack((datac,rows[i]))    
    for i in range(number_of_atoms):
        if props['_atomic_numbers'][i] == 6:
            datacae = np.vstack((datacae,yi[0][i]))
            
    for i in range(number_of_atoms):
        if props['_atomic_numbers'][i] == 7:
            datan = np.vstack((datan,rows[i]))    
    for i in range(number_of_atoms):
        if props['_atomic_numbers'][i] == 7:
            datanae = np.vstack((datanae,yi[0][i]))

U0 of hyrogen: -13.61 eV
U0 of carbon: -1029.86 eV
U0 of oxygen: -2042.61 eV
U0 of oxygen: -1485.30 eV
None
0
C -2.8340169e-06 2.3049886e-06 -1.4378233e-07
H 0.014845718 -1.0918331 -0.0060250196
H 1.0244261 0.3779494 -0.007724565
H -0.52811974 0.36172476 -0.88464487
H -0.5111183 0.3521308 0.89839613



/home/amerelsamman/Programs/anaconda3/lib/python3.7/site-packages/schnetpack/data/atoms.py:327: UserWarning: The given NumPy array is not writeable, and PyTorch does not support non-writeable tensors. This means you can write to the underlying (supposedly non-writeable) NumPy array using the tensor. You may want to copy the array to protect its data or make it writeable before converting it to a tensor. This type of warning will be suppressed for the rest of this program. (Triggered internally at  /pytorch/torch/csrc/utils/tensor_numpy.cpp:141.)
  properties[pname] = torch.FloatTensor(prop)
/home/amerelsamman/Programs/anaconda3/lib/python3.7/site-packages/ase/atoms.py:972: VisibleDeprecationWarning: Use get_global_number_of_atoms() instead
  np.VisibleDeprecationWarning)


1
N -0.03160822 0.021159047 0.060332563
H 0.026075294 -0.9904034 -0.029608395
H 0.9246072 0.35579658 -0.030988995
H -0.5114599 0.34058344 -0.77777386

2
O -0.056248687 0.035458494 0.0007260183
H 0.042878296 -0.9215089 -0.00534094
H 0.84990215 0.35871136 -0.0061824406

3
C 0.5995395 0.0 0.0
C -0.5995395 0.0 0.0
H -1.6616386 0.0 0.0
H 1.6616386 0.0 0.0

4
C -0.0075630867 0.5570853 0.003070365
N 0.008071566 -0.59453905 -0.0032767907
H -0.022041854 1.6235689 0.008948269

5
C -0.008137181 0.5992856 0.002790173
O 0.0081545 -0.60058945 -0.0028012523
H 0.9208008 1.2085854 -0.0010057696
H -0.9532692 1.1830921 0.012220519

6
C -0.010403622 0.7647314 0.004216852
C 0.010404125 -0.7647325 -0.004217135
H 1.0031731 1.1788927 -0.0032747546
H -0.53377575 1.1627601 -0.8713333
H -0.5169408 1.1533226 0.89380807
H 0.5337869 -1.1627584 0.871328
H -1.0031761 -1.1788844 0.0032925315
H 0.5169266 -1.1533209 -0.8938171

7
C -0.013109998 0.7242496 0.009729234
O -0.012792213 -0.6912656 0.03563598
H 1.0017616 1.149

34
C -0.25688466 1.5916414 -0.86591065
C -0.61305434 0.1284587 -0.56164634
C 0.08349835 -0.37345108 0.6828184
O 0.7562327 -1.3691448 0.7497238
H 0.805587 1.6978836 -1.104767
H -0.83312476 1.9608278 -1.7181325
H -0.47498843 2.2391737 -0.009865776
H -1.6947297 0.049830392 -0.37989575
H -0.36288747 -0.53599375 -1.3931805
H -0.071829684 0.27314475 1.5802705

35
C -0.29365814 1.3020542 -0.8425833
N -0.12132652 -0.13851523 -0.8365585
C 0.14862932 -0.8454173 0.29319996
O 0.27617267 -0.3755904 1.4037071
H 0.45184562 1.7905327 -1.4794713
H -1.2930315 1.5830164 -1.1923411
H -0.1657088 1.6470488 0.18400396
H -0.2045438 -0.64620566 -1.7021039
H 0.24206837 -1.9293629 0.08119238

36
C -0.34122062 1.6519755 0.5416211
O -0.020892803 0.26402432 0.60135955
C 0.059390184 -0.41967162 -0.5549229
O 0.3215117 -1.5826951 -0.6018447
H 0.47573406 2.2207065 0.99291736
H -0.4853366 1.9861269 -0.49231416
H -1.2604542 1.8248742 1.106993
H -0.14317384 0.214536 -1.4413954

37
O 0.9053031 1.4252946 0.50014365
C 0.7614

62
C 0.5450326 1.5968091 -0.2746015
C 0.55363744 0.06308237 -0.24318773
N 1.3183624 -0.415496 0.9106862
C -0.8297439 -0.46547034 -0.28376332
N -1.9011331 -0.9008385 -0.2748727
H 1.5761107 1.9565881 -0.27789873
H 0.026943982 1.9674567 -1.1621372
H 0.037180185 1.9970266 0.60830957
H 1.0598638 -0.30253276 -1.1445831
H 0.85638237 -0.12812711 1.7697307
H 1.3371655 -1.4311808 0.9224594

63
C -0.024941536 1.5804 0.6270696
C -0.005323342 0.045704123 0.5899224
O -1.3089012 -0.5031127 0.7618272
C 0.63353485 -0.45244792 -0.6337418
C 1.121628 -0.8410348 -1.661492
H 0.9908436 1.9844332 0.5898606
H -0.5801212 1.9766587 -0.22921759
H -0.5106804 1.9140329 1.5476044
H 0.5607209 -0.3199105 1.4551519
H -1.802564 -0.33429405 -0.048530698
H 1.56339 -1.198912 -2.5586312

64
C 0.5316238 1.5948187 -0.28219584
C 0.54895324 0.06251989 -0.23920514
O 1.2624056 -0.45100507 0.86912805
C -0.82840264 -0.47825956 -0.28057352
N -1.9092673 -0.8870317 -0.28234872
H 1.5604715 1.9616041 -0.26227635
H 0.038933463 1.9549932 

...

9933
C -0.50588596 3.2512157 -1.153489
C -0.3398895 1.7300687 -1.1949902
C 0.27018833 1.1671214 0.09405266
C 0.40712035 -0.37265593 0.09852432
C 1.2961109 -0.8486603 1.2434262
O 1.3474342 -2.265111 1.1809775
C -0.9719293 -0.994567 0.2336732
O -1.6380239 -1.413871 -0.6757814
H 0.4558059 3.7529 -0.9969261
H -0.9295204 3.6289363 -2.0889173
H -1.1733133 3.5560176 -0.3396169
H -1.3092458 1.2541971 -1.3815728
H 0.29920626 1.4512445 -2.042298
H 1.2646116 1.6060306 0.24975382
H -0.33477166 1.4809089 0.95720947
H 0.83094686 -0.7100919 -0.8534363
H 2.2962682 -0.3997956 1.1449515
H 0.8756501 -0.5051246 2.2037868
H 1.8457104 -2.5889382 1.9370931
H -1.3645519 -0.9920476 1.2798842

9934
C 1.1054124 3.2096667 -0.53318316
C 1.1913139 1.6860421 -0.41402867
C -0.18497403 1.029416 -0.25859755
C -0.10799439 -0.49595684 -0.10497124
O 0.6091282 -0.7888698 1.0769497
C 1.0501958 -2.1292248 1.155963
C -1.5241473 -1.0610918 -0.024279067
O -2.2156103 -1.3080279 -0.9770435
H 2.0989912 3.6539965 -0.64713794
H 0.50

9945
C 2.4090748 1.9263985 0.020424329
C 1.9530168 0.47410947 -0.1327661
C 0.42986798 0.3096409 -0.191242
C 0.022633202 -1.1559227 -0.3782059
C -1.4836991 -1.3653679 -0.53580856
O -1.82738 -2.7272449 -0.74780345
O -0.14207362 0.80044496 1.0261787
C -1.038368 1.8788627 0.8808597
H 3.4999435 1.9923999 0.07466488
H 2.082263 2.5400076 -0.8270136
H 2.0000193 2.364829 0.9348267
H 2.384292 0.03770358 -1.0421379
H 2.3269057 -0.12138628 0.7095241
H 0.04136146 0.90092194 -1.035913
H 0.5298817 -1.5691185 -1.2578698
H 0.37692535 -1.7226174 0.49416777
H -2.0094595 -0.951298 0.3364593
H -1.8472698 -0.83164966 -1.4217279
H -1.5845902 -3.2152672 0.045464687
H -0.5588844 2.760981 0.43173924
H -1.9136393 1.613492 0.26860163
H -1.3855238 2.1449218 1.8833016

9946
C -0.07005783 2.8764162 -0.84064186
C -0.5038699 1.410559 -0.95897675
C -0.043306015 0.5009682 0.19778429
C -0.8418019 0.78497803 1.4727364
O -0.23148264 0.08558982 2.5494406
C -0.13891412 -0.99332875 -0.1626587
C 0.9892921 -1.4882681 -1.0590674

9957
C -0.8958131 2.3767922 -0.5379823
O -0.6940531 0.9782249 -0.5687156
C -0.0028983392 0.4461837 0.5688549
C -1.0209979 0.19726035 1.6902143
O -2.0777502 -0.62869936 1.2423463
C 0.6955114 -0.8367942 0.12065858
C 1.7073755 -0.6218149 -1.0058671
O 2.3969069 -1.8148072 -1.3497752
H 0.060658153 2.9177685 -0.49101502
H -1.4092524 2.6472046 -1.4639655
H -1.5153568 2.6969025 0.31154513
H 0.7476228 1.1758317 0.9147514
H -0.5386241 -0.31253085 2.5308993
H -1.4014285 1.1609188 2.0668828
H -2.3312097 -0.27506575 0.3800041
H 1.2108265 -1.2776277 0.981655
H -0.070843704 -1.5555022 -0.19359574
H 1.206269 -0.17796227 -1.8764892
H 2.4840243 0.081927866 -0.683545
H 1.7502899 -2.4327178 -1.7054011

9958
C 0.8478387 3.045463 0.2149875
O 0.8736359 1.63555 0.22814977
C -0.41671386 1.0540679 0.33402702
C -0.29694238 -0.4690037 0.28445262
C -1.6823133 -1.0970573 0.44580898
O -1.5150455 -2.4967458 0.60762596
C 0.3830931 -0.9544566 -1.0087296
O 1.7653612 -0.6724189 -1.0571184
H 1.8810993 3.3914049 0.1404979


9974
N 0.79885894 1.8843521 -0.33356795
C 1.0181959 0.5587242 -0.31889498
O 2.0720809 0.016162073 -0.584332
N -0.13332656 -0.2379317 0.051278897
C 0.07529048 -1.632428 0.07313027
N -0.85040903 -2.4430537 0.3806166
C -1.4006828 0.23423181 0.3806778
N -1.7236522 1.467405 0.40038
H 1.5806785 2.4630342 -0.5872219
H -0.12012204 2.2541976 -0.096342005
H 1.1007301 -1.8704349 -0.20196795
H -0.5044205 -3.399 0.33830562
H -2.0656292 -0.59671575 0.6157713
H -2.6982965 1.5743362 0.66844916

9975
N 2.0624592 -0.18207544 -0.28114012
C 1.030249 0.6540525 -0.08608228
O 1.099001 1.8621764 -0.0066464404
N -0.2597208 -0.0050716386 0.03317366
C -0.51552165 -1.374951 -0.033227243
N 0.38062912 -2.2602239 -0.2133634
C -1.37494 0.8388653 0.23923303
O -2.5028803 0.4320853 0.35594332
H 2.971237 0.23954359 -0.3680935
H 1.9064397 -1.1867193 -0.33452803
H -1.5819663 -1.565538 0.09110898
H -0.031084664 -3.1897295 -0.22740825
H -1.0719203 1.8904732 0.27646515

9976
N 1.1305659 2.0097544 0.022197919
C 1.191087 0.6564

9991
C 0.9723172 2.0453603 -0.17243443
C 1.0824941 0.51723343 -0.22373267
C 2.1523395 -0.036567897 0.72425205
N -0.23110548 -0.12860885 0.00541075
C -0.8214846 -0.8954612 -0.99840105
N -0.26542142 -1.0669295 -2.1285224
C -0.89777476 0.011373848 1.2079992
O -1.9702716 -0.48156467 1.4758346
H 1.9283425 2.4945877 -0.45783788
H 0.2067469 2.4029498 -0.86638147
H 0.72394073 2.4082625 0.83044875
H 1.339934 0.22427772 -1.2427055
H 1.9579451 0.23112126 1.7681468
H 2.207105 -1.1263163 0.6536822
H 3.131147 0.37245813 0.4561506
H -1.7810302 -1.2993232 -0.67329687
H -0.8504186 -1.6532929 -2.7202473
H -0.3367633 0.6368785 1.9231055

9992
C 1.389542 1.9671878 -0.19870317
C 1.35917 0.4357371 -0.118535936
C 2.1668534 -0.11331631 1.0642068
N -0.024994325 -0.09291412 -0.1374915
C -0.41740817 -0.89590925 -1.2191604
O -1.491347 -1.3997017 -1.3882865
C -0.88826424 0.22535239 0.9182356
O -2.029149 -0.12634523 1.0403991
H 2.4214742 2.313302 -0.3093907
H 0.81280386 2.3242643 -1.0562681
H 0.9809625 2.4309323 0.

In [4]:
print('DONE')  
savetxt('../../../../data/dataO.csv',datao,delimiter=',')
savetxt('../../../../data/dataH.csv',datah,delimiter=',')
savetxt('../../../../data/hae.csv',datahae,delimiter=',')
savetxt('../../../../data/oae.csv',dataoae,delimiter=',')

savetxt('../../../../data/dataC.csv',datac,delimiter=',')
savetxt('../../../../data/cae.csv',datacae,delimiter=',')

savetxt('../../../../data/dataN.csv',datan,delimiter=',')
savetxt('../../../../data/nae.csv',datanae,delimiter=',')

DONE
